In [2]:
import numpy as np
import pandas as pd
import gc
import time
import matplotlib.pyplot as plt
import seaborn as sns
#import warning
%matplotlib inline

#warning.ignorewarning(...)

pd.set_option('display.max_rows', 100)
pd.set_option('display.max_columns', 200)

In [3]:
train = pd.read_csv("../input/dacon-bus-dataset/train.csv")
test = pd.read_csv("../input/dacon-bus-dataset/test.csv")

In [4]:
train.head()

id        date  bus_route_id in_out  station_code  station_name  latitude  \
0   0  2019-09-01       4270000     시외           344         제주썬호텔  33.48990   
1   1  2019-09-01       4270000     시외           357          한라병원  33.48944   
2   2  2019-09-01       4270000     시외           432          정존마을  33.48181   
3   3  2019-09-01       4270000     시내          1579  제주국제공항(600번)  33.50577   
4   4  2019-09-01       4270000     시내          1646      중문관광단지입구  33.25579   

   longitude  6~7_ride  7~8_ride  8~9_ride  9~10_ride  10~11_ride  11~12_ride  \
0  126.49373       0.0       1.0       2.0        5.0         2.0         6.0   
1  126.48508       1.0       4.0       4.0        2.0         5.0         6.0   
2  126.47352       1.0       1.0       0.0        2.0         0.0         0.0   
3  126.49252       0.0      17.0       6.0       26.0        14.0        16.0   
4  126.41260       0.0       0.0       0.0        0.0         0.0         0.0   

   6~7_takeoff  7~8_takeoff  8~9_takeoff  9~10_takeoff  10~11_takeoff  \
0          0.0          0.0          0.0           0.0            0.0   
1          0.0          0.0          0.0           0.0            0.0   
2          0.0          0.0          0.0           0.0            0.0   
3          0.0          0.0          0.0           0.0            0.0   
4          0.0          0.0          0.0           1.0            0.0   

   11~12_takeoff  18~20_ride  
0            0.0         0.0  
1            0.0         5.0  
2            0.0         2.0  
3            0.0        53.0  
4            0.0         0.0

In [5]:
test.head()
# 퇴근시간 버스 정류장별 버스 승차인원 값이 없음

id        date  bus_route_id in_out  station_code  station_name  \
0  415423  2019-10-01       4270000     시외           344         제주썬호텔   
1  415424  2019-10-01       4270000     시외           357          한라병원   
2  415425  2019-10-01       4270000     시외           432          정존마을   
3  415426  2019-10-01       4270000     시내          1579  제주국제공항(600번)   
4  415427  2019-10-01       4270000     시내          1636          롯데호텔   

   latitude  longitude  6~7_ride  7~8_ride  8~9_ride  9~10_ride  10~11_ride  \
0  33.48990  126.49373       4.0       4.0       7.0        2.0         9.0   
1  33.48944  126.48508       1.0       6.0       6.0        1.0         8.0   
2  33.48181  126.47352       2.0       4.0       2.0        2.0         2.0   
3  33.50577  126.49252       1.0      11.0      18.0        8.0        26.0   
4  33.24872  126.41032       0.0       0.0       0.0        0.0         0.0   

   11~12_ride  6~7_takeoff  7~8_takeoff  8~9_takeoff  9~10_takeoff  \
0         1.0          0.0          0.0          0.0           0.0   
1        11.0          0.0          0.0          0.0           0.0   
2         1.0          0.0          0.0          0.0           0.0   
3        20.0          0.0          0.0          0.0           0.0   
4         0.0          0.0          0.0          0.0           1.0   

   10~11_takeoff  11~12_takeoff  
0            0.0            1.0  
1            0.0            0.0  
2            0.0            0.0  
3            0.0            0.0  
4            0.0            0.0

In [6]:
# 단위 통일(1시간 -> 2시간으로)
train['68a']=train['6~7_ride']+train['7~8_ride'] # 6 ~ 8시 승차인원
train['810a']=train['8~9_ride']+train['9~10_ride']
train['1012a']=train['10~11_ride']+train['11~12_ride']

train['68b']=train['6~7_takeoff']+train['7~8_takeoff'] # 6 ~ 8시 하차인원
train['810b']=train['8~9_takeoff']+train['9~10_takeoff']
train['1012b']=train['10~11_takeoff']+train['11~12_takeoff']

In [7]:
test['68a']=test['6~7_ride']+test['7~8_ride']
test['810a']=test['8~9_ride']+test['9~10_ride']
test['1012a']=test['10~11_ride']+test['11~12_ride']

test['68b']=test['6~7_takeoff']+test['7~8_takeoff']
test['810b']=test['8~9_takeoff']+test['9~10_takeoff']
test['1012b']=test['10~11_takeoff']+test['11~12_takeoff']

In [8]:
train.shape, test.shape

((415423, 27), (228170, 26))

In [9]:
train.head()
# 뒤에 추가됨

id        date  bus_route_id in_out  station_code  station_name  latitude  \
0   0  2019-09-01       4270000     시외           344         제주썬호텔  33.48990   
1   1  2019-09-01       4270000     시외           357          한라병원  33.48944   
2   2  2019-09-01       4270000     시외           432          정존마을  33.48181   
3   3  2019-09-01       4270000     시내          1579  제주국제공항(600번)  33.50577   
4   4  2019-09-01       4270000     시내          1646      중문관광단지입구  33.25579   

   longitude  6~7_ride  7~8_ride  8~9_ride  9~10_ride  10~11_ride  11~12_ride  \
0  126.49373       0.0       1.0       2.0        5.0         2.0         6.0   
1  126.48508       1.0       4.0       4.0        2.0         5.0         6.0   
2  126.47352       1.0       1.0       0.0        2.0         0.0         0.0   
3  126.49252       0.0      17.0       6.0       26.0        14.0        16.0   
4  126.41260       0.0       0.0       0.0        0.0         0.0         0.0   

   6~7_takeoff  7~8_takeoff  8~9_takeoff  9~10_takeoff  10~11_takeoff  \
0          0.0          0.0          0.0           0.0            0.0   
1          0.0          0.0          0.0           0.0            0.0   
2          0.0          0.0          0.0           0.0            0.0   
3          0.0          0.0          0.0           0.0            0.0   
4          0.0          0.0          0.0           1.0            0.0   

   11~12_takeoff  18~20_ride   68a  810a  1012a  68b  810b  1012b  
0            0.0         0.0   1.0   7.0    8.0  0.0   0.0    0.0  
1            0.0         5.0   5.0   6.0   11.0  0.0   0.0    0.0  
2            0.0         2.0   2.0   2.0    0.0  0.0   0.0    0.0  
3            0.0        53.0  17.0  32.0   30.0  0.0   0.0    0.0  
4            0.0         0.0   0.0   0.0    0.0  0.0   1.0    0.0

In [10]:
# in_out: 시내, 시외 변수 -> 0, 1로!
train['in_out'].value_counts()
# 시내: 0, 시외: 1

시내    408500
시외      6923
Name: in_out, dtype: int64

In [11]:
train['in_out'] = train['in_out'].map({'시내':0,'시외':1})
test['in_out'] = test['in_out'].map({'시내':0,'시외':1})

In [12]:
# 출퇴근 -> 평일만 보고 싶음
# date -> date2로 datetime 변수형 변환 -> weekday 변수 생성
train['date2'] = pd.to_datetime(train['date'])
train['weekday'] = train['date2'].dt.weekday
# 월화수목금토일 = 0123456

In [13]:
train.head()

id        date  bus_route_id  in_out  station_code  station_name  latitude  \
0   0  2019-09-01       4270000       1           344         제주썬호텔  33.48990   
1   1  2019-09-01       4270000       1           357          한라병원  33.48944   
2   2  2019-09-01       4270000       1           432          정존마을  33.48181   
3   3  2019-09-01       4270000       0          1579  제주국제공항(600번)  33.50577   
4   4  2019-09-01       4270000       0          1646      중문관광단지입구  33.25579   

   longitude  6~7_ride  7~8_ride  8~9_ride  9~10_ride  10~11_ride  11~12_ride  \
0  126.49373       0.0       1.0       2.0        5.0         2.0         6.0   
1  126.48508       1.0       4.0       4.0        2.0         5.0         6.0   
2  126.47352       1.0       1.0       0.0        2.0         0.0         0.0   
3  126.49252       0.0      17.0       6.0       26.0        14.0        16.0   
4  126.41260       0.0       0.0       0.0        0.0         0.0         0.0   

   6~7_takeoff  7~8_takeoff  8~9_takeoff  9~10_takeoff  10~11_takeoff  \
0          0.0          0.0          0.0           0.0            0.0   
1          0.0          0.0          0.0           0.0            0.0   
2          0.0          0.0          0.0           0.0            0.0   
3          0.0          0.0          0.0           0.0            0.0   
4          0.0          0.0          0.0           1.0            0.0   

   11~12_takeoff  18~20_ride   68a  810a  1012a  68b  810b  1012b      date2  \
0            0.0         0.0   1.0   7.0    8.0  0.0   0.0    0.0 2019-09-01   
1            0.0         5.0   5.0   6.0   11.0  0.0   0.0    0.0 2019-09-01   
2            0.0         2.0   2.0   2.0    0.0  0.0   0.0    0.0 2019-09-01   
3            0.0        53.0  17.0  32.0   30.0  0.0   0.0    0.0 2019-09-01   
4            0.0         0.0   0.0   0.0    0.0  0.0   1.0    0.0 2019-09-01   

   weekday  
0        6  
1        6  
2        6  
3        6  
4        6

In [14]:
# 평일 데이터만 모으기
train_weekdays = train[train['weekday'] < 5]
train_weekends = train[train['weekday'] > 4]

In [15]:
train_weekdays.head()

id        date  bus_route_id  in_out  station_code  station_name  \
11538  11538  2019-09-02       4270000       1           344         제주썬호텔   
11539  11539  2019-09-02       4270000       1           357          한라병원   
11540  11540  2019-09-02       4270000       1           432          정존마을   
11541  11541  2019-09-02       4270000       0          1579  제주국제공항(600번)   
11542  11542  2019-09-02       4270000       0          1636          롯데호텔   

       latitude  longitude  6~7_ride  7~8_ride  8~9_ride  9~10_ride  \
11538  33.48990  126.49373       1.0       8.0       3.0        3.0   
11539  33.48944  126.48508       1.0       3.0       1.0        2.0   
11540  33.48181  126.47352       0.0       4.0       0.0        1.0   
11541  33.50577  126.49252       1.0      12.0      17.0       21.0   
11542  33.24872  126.41032       0.0       0.0       0.0        0.0   

       10~11_ride  11~12_ride  6~7_takeoff  7~8_takeoff  8~9_takeoff  \
11538         0.0         4.0          0.0          0.0          0.0   
11539         8.0         9.0          0.0          0.0          0.0   
11540         0.0         1.0          0.0          0.0          0.0   
11541        19.0        16.0          0.0          0.0          0.0   
11542         0.0         0.0          0.0          0.0          0.0   

       9~10_takeoff  10~11_takeoff  11~12_takeoff  18~20_ride   68a  810a  \
11538           0.0            0.0            0.0         1.0   9.0   6.0   
11539           0.0            0.0            0.0         6.0   4.0   3.0   
11540           0.0            1.0            0.0         2.0   4.0   1.0   
11541           0.0            0.0            2.0        62.0  13.0  38.0   
11542           3.0            0.0            0.0         0.0   0.0   0.0   

       1012a  68b  810b  1012b      date2  weekday  
11538    4.0  0.0   0.0    0.0 2019-09-02        0  
11539   17.0  0.0   0.0    0.0 2019-09-02        0  
11540    1.0  0.0   0.0    1.0 2019-09-02        0  
11541   35.0  0.0   0.0    2.0 2019-09-02        0  
11542    0.0  0.0   3.0    0.0 2019-09-02        0

In [16]:
train_weekends.head()

id        date  bus_route_id  in_out  station_code  station_name  latitude  \
0   0  2019-09-01       4270000       1           344         제주썬호텔  33.48990   
1   1  2019-09-01       4270000       1           357          한라병원  33.48944   
2   2  2019-09-01       4270000       1           432          정존마을  33.48181   
3   3  2019-09-01       4270000       0          1579  제주국제공항(600번)  33.50577   
4   4  2019-09-01       4270000       0          1646      중문관광단지입구  33.25579   

   longitude  6~7_ride  7~8_ride  8~9_ride  9~10_ride  10~11_ride  11~12_ride  \
0  126.49373       0.0       1.0       2.0        5.0         2.0         6.0   
1  126.48508       1.0       4.0       4.0        2.0         5.0         6.0   
2  126.47352       1.0       1.0       0.0        2.0         0.0         0.0   
3  126.49252       0.0      17.0       6.0       26.0        14.0        16.0   
4  126.41260       0.0       0.0       0.0        0.0         0.0         0.0   

   6~7_takeoff  7~8_takeoff  8~9_takeoff  9~10_takeoff  10~11_takeoff  \
0          0.0          0.0          0.0           0.0            0.0   
1          0.0          0.0          0.0           0.0            0.0   
2          0.0          0.0          0.0           0.0            0.0   
3          0.0          0.0          0.0           0.0            0.0   
4          0.0          0.0          0.0           1.0            0.0   

   11~12_takeoff  18~20_ride   68a  810a  1012a  68b  810b  1012b      date2  \
0            0.0         0.0   1.0   7.0    8.0  0.0   0.0    0.0 2019-09-01   
1            0.0         5.0   5.0   6.0   11.0  0.0   0.0    0.0 2019-09-01   
2            0.0         2.0   2.0   2.0    0.0  0.0   0.0    0.0 2019-09-01   
3            0.0        53.0  17.0  32.0   30.0  0.0   0.0    0.0 2019-09-01   
4            0.0         0.0   0.0   0.0    0.0  0.0   1.0    0.0 2019-09-01   

   weekday  
0        6  
1        6  
2        6  
3        6  
4        6

In [17]:
# test 데이터도 똑같이
test['date2'] = pd.to_datetime(test['date'])
test['weekday'] = test['date2'].dt.weekday
test_weekdays = test[test['weekday'] < 5]
test_weekends = test[test['weekday'] > 4]

In [18]:
del train_weekdays['date2']
del test_weekdays['date2']

# 근처 정류장끼리 묶기

In [19]:
train_weekdays['location'] = train_weekdays['latitude'].astype(str) + ',' + train_weekdays['longitude'].astype(str)
test_weekdays['location'] = test_weekdays['latitude'].astype(str) + ',' + test_weekdays['longitude'].astype(str)

/opt/conda/lib/python3.7/site-packages/ipykernel_launcher.py:1: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  """Entry point for launching an IPython kernel.
/opt/conda/lib/python3.7/site-packages/ipykernel_launcher.py:2: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  


In [20]:
train_weekdays.info()

<class 'pandas.core.frame.DataFrame'>
Int64Index: 317330 entries, 11538 to 415422
Data columns (total 29 columns):
 #   Column         Non-Null Count   Dtype  
---  ------         --------------   -----  
 0   id             317330 non-null  int64  
 1   date           317330 non-null  object 
 2   bus_route_id   317330 non-null  int64  
 3   in_out         317330 non-null  int64  
 4   station_code   317330 non-null  int64  
 5   station_name   317330 non-null  object 
 6   latitude       317330 non-null  float64
 7   longitude      317330 non-null  float64
 8   6~7_ride       317330 non-null  float64
 9   7~8_ride       317330 non-null  float64
 10  8~9_ride       317330 non-null  float64
 11  9~10_ride      317330 non-null  float64
 12  10~11_ride     317330 non-null  float64
 13  11~12_ride     317330 non-null  float64
 14  6~7_takeoff    317330 non-null  float64
 15  7~8_takeoff    317330 non-null  float64
 16  8~9_takeoff    317330 non-null  float64
 17  9~10_takeoff   317330 non

In [21]:
train_weekdays = pd.DataFrame(train_weekdays)
train_weekdays

id        date  bus_route_id  in_out  station_code  station_name  \
11538    11538  2019-09-02       4270000       1           344         제주썬호텔   
11539    11539  2019-09-02       4270000       1           357          한라병원   
11540    11540  2019-09-02       4270000       1           432          정존마을   
11541    11541  2019-09-02       4270000       0          1579  제주국제공항(600번)   
11542    11542  2019-09-02       4270000       0          1636          롯데호텔   
...        ...         ...           ...     ...           ...           ...   
415418  415418  2019-09-30      32820000       0          1129  한림환승정류장(한림리)   
415419  415419  2019-09-30      32820000       0          1564     제주시외버스터미널   
415420  415420  2019-09-30      32820000       0          2322          해병부대   
415421  415421  2019-09-30      32820000       0          3291  애월환승정류장(애월리)   
415422  415422  2019-09-30      32820000       0       6115100    서귀포시외버스터미널   

        latitude  longitude  6~7_ride  7~8_ride  8~9_ride  9~10_ride  \
11538   33.48990  126.49373       1.0       8.0       3.0        3.0   
11539   33.48944  126.48508       1.0       3.0       1.0        2.0   
11540   33.48181  126.47352       0.0       4.0       0.0        1.0   
11541   33.50577  126.49252       1.0      12.0      17.0       21.0   
11542   33.24872  126.41032       0.0       0.0       0.0        0.0   
...          ...        ...       ...       ...       ...        ...   
415418  33.41437  126.26336       4.0       0.0       0.0        0.0   
415419  33.49946  126.51479       4.0       0.0       0.0        0.0   
415420  33.23100  126.26273       0.0       0.0       0.0        0.0   
415421  33.46483  126.31870       1.0       0.0       0.0        0.0   
415422  33.24873  126.50799       0.0       0.0       0.0        0.0   

        10~11_ride  11~12_ride  6~7_takeoff  7~8_takeoff  8~9_takeoff  \
11538          0.0         4.0          0.0          0.0          0.0   
11539          8.0         9.0          0.0          0.0          0.0   
11540          0.0         1.0          0.0          0.0          0.0   
11541         19.0        16.0          0.0          0.0          0.0   
11542          0.0         0.0          0.0          0.0          0.0   
...            ...         ...          ...          ...          ...   
415418         0.0         0.0          0.0          0.0          0.0   
415419         0.0         0.0          0.0          0.0          0.0   
415420         0.0         0.0          0.0          1.0          0.0   
415421         0.0         0.0          0.0          0.0          0.0   
415422         0.0         0.0          0.0          0.0          4.0   

        9~10_takeoff  10~11_takeoff  11~12_takeoff  18~20_ride   68a  810a  \
11538            0.0            0.0            0.0         1.0   9.0   6.0   
11539            0.0            0.0            0.0         6.0   4.0   3.0   
11540            0.0            1.0            0.0         2.0   4.0   1.0   
11541            0.0            0.0            2.0        62.0  13.0  38.0   
11542            3.0            0.0            0.0         0.0   0.0   0.0   
...              ...            ...            ...         ...   ...   ...   
415418           0.0            0.0            0.0         0.0   4.0   0.0   
415419           0.0            0.0            0.0         0.0   4.0   0.0   
415420           0.0            0.0            0.0         0.0   0.0   0.0   
415421           0.0            0.0            0.0         0.0   1.0   0.0   
415422           0.0            0.0            0.0         0.0   0.0   0.0   

        1012a  68b  810b  1012b  weekday            location  
11538     4.0  0.0   0.0    0.0        0   33.4899,126.49373  
11539    17.0  0.0   0.0    0.0        0  33.48944,126.48508  
11540     1.0  0.0   0.0    1.0        0  33.48181,126.47352  
11541    35.0  0.0   0.0    2.0        0  33.50577,126.49252  
11542     0.0  0.0   3.0    0.0        0  33.24872,126.41

In [ ]:
# 제주도 공공기관 크롤링
from bs4 import BeautifulSoup as bs
import time
import numpy as np
import pandas as pd
import requests
import random
name=[];address=[];roadaddress=[];abbraddress=[];tel=[];x=[];y=[]; value='';count ='0'
passing = ['']

korea_sep = ['서울','부산','대구','인천','광주광역시','대전','울산','세종','경기','강원','충청북도','충청남도','전라북도','전라남도','경상북도','경상남도','제주도']
seoul_sep = ['강서구','양천구','구로구','영등포구','동작구','금천구','관악구','서초구','강남구','송파구','강동구',
            '마포구','용산구','성동구','광진구','서대문구','중구','은평구','종로구','동대문구','중랑구','성북구','강북구','도봉구','노원구']
busan_sep = ['중구','서구','동구','영도구','부산진구','동래구','남구','북구','해운대구','사하구','금정구','강서구','연제구','수영구','사상구','기장군']
daegu_sep = ['북구','동구','서구','중구','남구','달서구','수성구','달성군']
incheon_sep = ['강화군', '계양구','남동구','동구','미추홀구','부평구','서구','연수구','옹진군','중구']
gwangju_sep = ['동구','서구','남구','북구','광산구']
daegeon_sep = ['동구','중구','서구','유성구','대덕구']
ulsan_sep = ['중구','남구','동구','북구','울주군']
gyeongi_sep = ['수원','성남','용인','안양','안산','과천','광명','광주','군포','부천','시흥','김포','안성','오산',
            '의왕','이천','평택','하남','화성','여주','양평','고양','구리','남양주','동두천','양주','의정부','파주','포천','연천','가평']
gangwon_sep = ['원주','춘천','강릉','동해','속초','삼척','태백','홍천','철원','횡성','평창','정선','영월','인제','고성','양양','화천','양구']
chungbuk_sep = ['청주','충주','제천','보은','옥천','영동','증평','진천','괴산','음성','단양']
chungnam_sep = ['천안','공주','보령','아산','서산','논산','계룡','당진','금산','부여','서천','청양','홍성','예산','태안']
jeonrabuk_sep = ['전주','익산','군산','정읍','김제','남원','완주','고창','부안','임실','순창','진안','무주','장수']
jeonranam_sep = ['목포','여수','순천','나주','광양','담양','곡성','구례','고흥','보성','화순','장흥','강진','해남','영암','무안','함평','영광','장성','완도','진도','신안']
gyeongsangnam_sep = ['창원','김해','진주','양산','거제','통영','사천','밀양','함안','거창','창녕','고성','하동','합천','남해','함양','산청','의령']
gyeongsangbuk_sep = ['포항','경주','김천','안동','구미','영주','영천','상주','문경','경산','군위','의성','청송','영양','영덕','청도','고령','성주','칠곡','예천','봉화','울진','울릉']
jeju_sep = ['제주시','서귀포시']

start = time.time()
while value != 'end':
    print('검색어를 입력하세요. / end 입력시 종료 후 파일을 저장합니다.')
    ser=input()
    alpha  = random.randint(1000,9999)
    alpha = str(alpha)
    custom_header = {
    'referer' : 'https://map.naver.com/v5/?c=14139193.6935029,4517752.1016367,15,0,0,0,dh',
    'user-agent' : 'Mozilla/5.0 (Macintosh; Intel Mac OS X 10_14_4) AppleWebKit/537.36 (KHTML, like Gecko) Chrome/73.0.'+alpha+'.103 Safari/537.36'  }
    try:
        if ser!= 'end':
            flag =''
            yyy = len(name)
            for k in range(15):
                url='https://map.naver.com/v5/api/search?caller=pcweb&query='+ser+'&type=all&searchCoord=126.97826385498048;37.56842621812477&page='+str(k+1)+'&displayCount=20&isPlaceRecommendationReplace=true&lang=ko'
                headers=custom_header
                res = requests.get(url = url,headers=headers)
                a=res.json()
                result = a['result']
                place = result['place']
                for i in place['list']:
                    a=(i["name"]) ;name.append(a)
                    b=(i["address"]);address.append(b)
                    c=(i["roadAddress"]);roadaddress.append(c)
                    e=(i["telDisplay"]);tel.append(e)
            zzz = len(name)
            length = zzz-yyy
            print('자료의 수는 %d개입니다.'%length)
            if (length) == 300:
                print("저장 하시겠습니까? n을 누를경우 전국 단위 조사가 시작됩니다. (1시간 소요)")
                print("y/n")
                qqq = input()
                if qqq == 'y':
                    continue
                else:
                    print('자동 분류를 시작합니다.')
                    name=[];address=[];roadaddress=[];tel=[]
                    for sido in korea_sep:
                        if sido == '서울':
                            target = seoul_sep
                        elif sido == '부산':
                            target = busan_sep
                        elif sido == '대구':
                            target = daegu_sep
                        elif sido == '인천':
                            target = incheon_sep
                        elif sido == '광주광역시':
                            target = gwangju_sep
                        elif sido == '대전':
                            target = daegeon_sep
                        elif sido == '울산':
                            target = ulsan_sep
                        elif sido == '세종':
                            target = passing
                        elif sido == '경기':
                            target = gyeongi_sep
                        elif sido == '강원':
                            target = gangwon_sep
                        elif sido == '충청북도':
                            target = chungbuk_sep
                        elif sido == '충청남도':
                            target = chungnam_sep
                        elif sido == '전라북도':
                            target = jeonrabuk_sep
                        elif sido == '전라남도':
                            target = jeonranam_sep
                        elif sido == '경상북도':
                            target = gyeongsangbuk_sep
                        elif sido == '경상남도':
                            target = gyeongsangnam_sep
                        elif sido == '제주도':
                            target = jeju_sep
                        for gugun in target:
                            url ='https://map.naver.com/v5/api/search?caller=pcweb&query='+sido+gugun+ser+'&type=all&searchCoord=126.97826385498048;37.56842621812477&page=1&displayCount=20&isPlaceRecommendationReplace=true&lang=ko'
                            res = requests.get(url = url, headers = headers)
                            is_check = res.json()
                            if is_check['result']['place'] != None:
                                for k in range(15):
                                    alpha = random.randint(1000,9999)
                                    alpha = str(alpha)
                                    custom_header = {'referer' : 'https://map.naver.com/v5/?c=14139193.6935029,4517752.1016367,15,0,0,0,dh',
                                                    'user-agent' : 'Mozilla/5.0 (Macintosh; Intel Mac OS X 10_14_4) AppleWebKit/537.36 (KHTML, like Gecko) Chrome/73.0.'+alpha+'.103 Safari/537.36'}
                                    url='https://map.naver.com/v5/api/search?caller=pcweb&query='+sido+gugun+ser+'&type=all&searchCoord=126.97826385498048;37.56842621812477&page='+str(k+1)+'&displayCount=20&isPlaceRecommendationReplace=true&lang=ko'
                                    headers=custom_header
                                    res = requests.get(url = url,headers=headers)
                                    a=res.json()
                                    if a['result']['place'] != None:
                                        result = a['result']
                                        place = result['place']
                                        for i in place['list']:
                                            a=(i["name"]) ;name.append(a)
                                            b=(i["address"]);address.append(b)
                                            c=(i["roadAddress"]);roadaddress.append(c)
                                            e=(i["telDisplay"]);tel.append(e)
                                            time.sleep(3)
                                    else:
                                        print('pass',k)
                                        break
                            else:
                                print(gugun,"자료는 없습니다.")
                            print(sido,gugun,'완료')
                        print(sido,"완료")
    except Exception as e:
        print('검색결과가 없습니다',e)
    DB = pd.DataFrame({'Name':name,'Address':address,'Roadaddress':roadaddress,'Tel':tel})
    DB=DB.replace(r'^\s+$', np.nan, regex=True)
    DB["Address"].replace('',np.NaN,inplace=True)
    DB["Roadaddress"].replace('',np.NaN,inplace=True)
    DB["Tel"].replace('',np.NaN,inplace=True)
    value = ser
    print("작업시간 : ",time.time()-start)



counting = int(len(name))
print('찾은 자료는 %d개 입니다.'%counting)
print("저장될 파일 이름을 입력하세요")
keyword = input()
# DB = DB.dropna(subset=['Tel'])
DB = DB.drop_duplicates('Address')
name = list(DB['Name'])
counting1 = int(len(name))
print("중복 제거 자료는 %d개 입니다."%counting1)
time.sleep(1)
DB.to_csv(keyword+' 중복 제거.csv', sep=",",encoding='utf-8-sig')


del DB






# %%


In [22]:
company_loc = pd.read_csv("../input/jejucompany-loc/jejucompany_loc.csv")
company_loc.shape

(237, 6)

In [23]:
company_loc['location'] = company_loc['latitude'].astype(str) + ',' + company_loc['longitude'].astype(str)
company_loc.shape

(237, 7)

In [24]:
company_loc.head()

Unnamed: 0                 Name                   도로명주소  \
0           0          제주고용복지플러스센터     제주특별자치도 제주시 중앙로 165   
1           1                제주세무서      제주특별자치도 제주시 청사로 59   
2           2  가족보건의원인구보건복지협회제주도지회   제주특별자치도 제주시 신대로13길 21   
3           3                하귀우체국  제주특별자치도 제주시 애월읍 항몽로 26   
4           4              제주우편집중국  제주특별자치도 제주시 1100로 3307   

                           지번주소   latitude   longitude  \
0       제주특별자치도 제주시 이도일동 1292-3  33.504381  126.527071   
1           제주특별자치도 제주시 도남동 662  33.490865  126.525059   
2         제주특별자치도 제주시 연동 312-50  33.487824  126.498894   
3  제주특별자치도 제주시 애월읍 하귀2리 1384-16  33.481152  126.404815   
4           제주특별자치도 제주시 노형동 707  33.481652  126.480318   

                  location  
0  33.50438122,126.5270712  
1  33.49086505,126.5250585  
2  33.48782372,126.4988943  
3  33.48115237,126.4048147  
4    33.481652,126.4803181

In [25]:
len(company_loc)

237

In [26]:
train_weekdays.iloc[0]['latitude']

33.4899

In [27]:
# 회사(공공기관) 근처 5개 정류장 찾기 
# 퇴근 후, 이 근처 5개 정류장에서 버스를 탑승하여 퇴근할 것이라 가정
# 변수 추가: nc(# of near company)

import math

# 점과 점 사이의 거리 구하는 함수
def distance(x1, y1, x2, y2):
    result = math.sqrt(math.pow(x1 - x2, 2) + math.pow(y1 - y2, 2))
    return result

for i in range(len(company_loc)):
    for j in range(len(train_weekdays)):
        x1 = train_weekdays.iloc[j]['latitude']
        y1 = company_loc.iloc[i]['latitude']
        x2 = train_weekdays.iloc[j]['longitude']
        y2 = company_loc.iloc[i]['longitude']
        d = distance(x1, y1, x2, y2)
        # 그 중 최솟값인 train_weekdays의 station_code..row의 nc 값에 1씩 += count.............
        print(d)
        
# 

131.5406144344175
131.53482394455392
131.5320454483974
131.5285388297068
131.65221063725133
131.64882111318462
131.6410304910866
131.66638530988877
131.66289634519362
131.61205143352484
131.70928657969714
131.7597014862617
131.65337823875882
131.6512058005835
131.6515596154394
131.6510642749066
131.65075999521497
131.56000276557344
131.67796395432038
131.65146054718417
131.72183186669093
131.72820408172575
131.69229003798245
131.53687427199566
131.77410016208833
131.71319446484014
131.5407204897236
131.53534005845006
131.53223633556752
131.65221063725133
131.64873619929395
131.64113662726288
131.6627406531764
131.6129569327032
131.71085821528453
131.6498259317045
131.6512058005835
131.6515596154394
131.66612345741325
131.6510642749066
131.65075999521497
131.7583558955059
131.76742119185147
131.77465262643528
131.55950776898527
131.67782947768842
131.65174359953912
131.7216477850364
131.72766597171298
131.69213431133724
131.5372277799589
131.529054918925
131.7678815554659
131.7142705694

131.55926734274288
131.55073956666945
131.55440941249668
131.55776115304482
131.55561857487385
131.54816578597854
131.55064764506326
131.54149823124865
131.54257293619884
131.54441126765968
131.53780046487663
131.54443247932653
131.54268606354665
131.5762821193398
131.57446455906705
131.5762184689452
131.55554786331777
131.57192567446634
131.57474037399157
131.5932778754492
131.55615598394203
131.54873851853387
131.86872547764156
131.8708518665804
131.87061087412764
131.86814427057502
131.8666274738411
131.7077291214027
131.55926734274288
131.56355972439175
131.56759058915532
131.578969608521
131.53563700160993
131.54028212834575
131.54111643028878
131.5442698566349
131.55906934499075
131.4363469547339
131.54522438400298
131.50155655022337
131.43118273505453
131.48258673962417
131.558489496145
131.48247366402714
131.48352668429644
131.50400925567894
131.42844881885196
131.5584258543541
131.52573925775627
131.4958455289185
131.48426168331818
131.48468572308826
131.48554794151366
131.505

131.5414133864951
131.54462338448195
131.54443247932653
131.54856174896057
131.55223153402906
131.4912090409043
131.46477146808604
131.45531007675115
131.44752384282327
131.43940602084328
131.43672845099573
131.54458096109013
131.51263296420495
131.51781453024373
131.43982285062467
131.48464331904958
131.55769751160625
131.5832343420893
131.49290529800757
131.59349714422552
131.59107106163242
131.54111643028878
131.5407770525885
131.5446021727843
131.46460894402415
131.4473330788331
131.4363469547339
131.57660037177428
131.54522438400298
131.57372198329608
131.57192567446634
131.51680364933483
131.49275687463583
131.5372136396221
131.59349714422552
131.5932778754492
131.59020107788305
131.58865209664847
131.62590342121715
131.61746329843655
131.58581588141516
131.61395440384007
131.61399684958775
131.60763721408873
131.635454923974
131.63042437966723
131.63051635695572
131.5530659117787
131.5531649061002
131.5505627944069
131.55615598394203
131.55485489207948
131.60441153182057
131.604

131.5676047327578
131.56831191481936
131.54231132957977
131.54468701959533
131.57142356102707
131.57488181776677
131.5741109510347
131.5392427934998
131.5695212049481
131.53600464645143
131.63580869661413
131.64579962751105
131.63333938337996
131.56013005071136
131.56433052933494
131.5545861899284
131.551750708577
131.548038512416
131.54284868427965
131.56215955815406
131.55805814683185
131.59837773724755
131.59378007221804
131.53909431776393
131.54257293619884
131.54441126765968
131.62852824677518
131.6321507333132
131.63436531020156
131.63757757404073
131.58853185685786
131.58343944884285
131.58109842177785
131.60896004959574
131.60702885569142
131.59946705369933
131.59873848390643
131.57573755584724
131.57058906687158
131.55913298709288
131.56073112108186
131.56102105012445
131.56140290886265
131.5644153888706
131.54371128457373
131.54170327296242
131.53482394455392
131.53401089252657
131.5368601316969
131.62431157132062
131.62213961156075
131.61844665459924
131.61573006262128
131.6

131.54022556569373
131.59440958918123
131.628266469375
131.58386380865738
131.57979708333949
131.6091369002684
131.6067246775456
131.6015325355905
131.5995519358789
131.59890824738173
131.5765579380719
131.54851225352263
131.56502355047746
131.53981548719457
131.53939126940338
131.53901654482632
131.54038111304524
131.54138510492274
131.55684189081006
131.5542609196376
131.5517082828862
131.55889963286896
131.54168913214428
131.54244566804888
131.54358401532204
131.5397447841343
131.54180932914673
131.52832673883483
131.53236359383493
131.53534005845006
131.5372136396221
131.6255921246153
131.62406395195217
131.62168682966646
131.61212924961623
131.61050926955184
131.60978771278675
131.56610551935324
131.5676047327578
131.56831191481936
131.54231132957977
131.57142356102707
131.57488181776677
131.5414133864951
131.54462338448195
131.54443247932653
131.54856174896057
131.5695212049481
131.53600464645143
131.53733383253322
131.52860245703513
131.63580869661413
131.64579962751105
131.6333

...

131.59449998861245
131.5946909428037
131.59636710814218
131.58683376017575
131.59136696494198
131.59174886451515
131.55901560750036
131.56045091985823
131.56071960075934
131.56251553456258
131.56618525507275
131.5590509598333
131.55583393644892
131.56347007628875
131.56197816597174
131.56431856363838
131.55535315729622
131.56239533350296
131.55984285458243
131.55465320255465
131.55171908938675
131.55451886823244
131.5566823745359
131.5580186756232
131.57626160367843
131.57435941282225
131.5718279152225
131.5676065038124
131.58571639514727
131.58459903960238
131.58247750454055
131.58256236528655
131.58426666351727
131.58263308261664
131.57884975881203
131.56368219761305
131.56108019967348
131.55241195839827
131.56176604739548
131.58753388613385
131.57389270848577
131.56740144707626
131.57169356335893
131.57572417893974
131.58085101748247
131.58710249495172
131.59136696494198
131.5626923010263
131.55987820713776
131.56251553456258
131.55583393644892
131.55535315729622
131.55465320255465


131.7150683044158
131.7406961701999
131.79938283198456
131.7973074292374
131.79559329854138
131.79348962294924
131.7828655083597
131.80103326074848
131.73124443221673
131.65956772810748
131.76377965376113
131.76714338044374
131.76957239825938
131.67649427789655
131.66734433086293
131.6704083956639
131.6721916716454
131.6627660570479
131.68522730103373
131.6786173260371
131.70026020950803
131.67959393963866
131.80431292902983
131.77413312336577
131.80286788161487
131.80325747618275
131.68120041394832
131.80224453268474
131.7641195633171
131.74931306151856
131.74739421468692
131.75071504098347
131.76098251447743
131.7719164780585
131.77166861267608
131.7381827208362
131.74178652645077
131.7338781071218
131.73714195436352
131.75232237913121
131.7661661205259
131.7679790142037
131.76326979106173
131.76008319362933
131.77338951617668
131.76134366078742
131.76423994816054
131.74227506560536
131.73668883410164
131.7383172422698
131.77297876351744
131.77415436934672
131.77253968449583
131.7372

131.49763002340433
131.49087399015386
131.50348176430964
131.50684592672172
131.51023137888407
131.51201955482597
131.49181387771037
131.49240042749287
131.49288097625714
131.4940399540486
131.49142520158844
131.5079767569805
131.50723464852427
131.50411783882709
131.50265487204592
131.50251352346245
131.5054182674346
131.50689540034173
131.4935382002113
131.5428535163812
131.54023779169674
131.5376786736064
131.53480856178004
131.5308074760226
131.59678438468632
131.5939483447264
131.56197816597174
131.5628973504218
131.56431856363838
131.55545921136996
131.55535315729622
131.55832270369262
131.5583792671319
131.54795079430932
131.54752660275307
131.5471519013503
131.54851638518022
131.54952031496893
131.54982432338906
131.55058081250885
131.55171908938675
131.54788009562157
131.54994451295838
131.49540388614966
131.5454692931236
131.53673845765533
131.52436782181326
131.4901743789764
131.499686583765
131.56740144707626
131.56826410170854
131.57169356335893
131.5724643206508
131.57572

131.87148247498254
131.87896675283147
131.87130529547406
131.87625932343553
131.6014098776378
131.55659753048087
131.76708672749817
131.71478515129925
131.75893603731066
131.68611903603554
131.84718273673096
131.87148247498254
131.85752853931749
131.87896675283147
131.87625932343553
131.53900771214037
131.56740144707626
131.57572417893974
131.60162913286493
131.63855408712192
131.55630057671934
131.61274089978687
131.7672141966598
131.68567316778248
131.87874703792164
131.87130529547406
131.8761530118866
131.85734429195867
131.8471189637317
131.53719089155894
131.56826410170854
131.57512311439777
131.581522824918
131.55630057671934
131.56726709973276
131.5695368811676
131.7672141966598
131.87874703792164
131.87130529547406
131.8761530118866
131.85734429195867
131.8471189637317
131.53719089155894
131.55659753048087
131.56738023432868
131.56967830186755
131.61742354177744
131.68149764922188
131.75955918272086
131.9040308070774
131.91249524346213
131.89908992315347
131.53900771214037
131.

KeyboardInterrupt: 

In [ ]:
# bus_bts:
# geton_date에 평일이 3번 이상 
# -> 직장인으로 구분(통학/통근) 
# -> 변수 생성(mover?)

In [ ]:
# 오전(승차시간 ride_on)의 날씨
# 날씨가 안 좋으면 대중교통
# 추우면? 자가용 타지 않을까.. 
# 이런 거는 시각화나 상관계수를 통해 분석해본 다음 적용해보면 재밌겠다

In [28]:
test_weekdays.dtypes

id                 int64
date              object
bus_route_id       int64
in_out             int64
station_code       int64
station_name      object
latitude         float64
longitude        float64
6~7_ride         float64
7~8_ride         float64
8~9_ride         float64
9~10_ride        float64
10~11_ride       float64
11~12_ride       float64
6~7_takeoff      float64
7~8_takeoff      float64
8~9_takeoff      float64
9~10_takeoff     float64
10~11_takeoff    float64
11~12_takeoff    float64
68a              float64
810a             float64
1012a            float64
68b              float64
810b             float64
1012b            float64
weekday            int64
location          object
dtype: object

Modeling

1. randomforest

In [29]:
input_var=['in_out','latitude', 'longitude', '68a', '810a', '1012a', '68b', '810b', '1012b']
           #'nc']

target=['18~20_ride']

In [30]:
import random #데이터 샘플링
from sklearn.model_selection import GridSearchCV #모델링
from sklearn.ensemble import RandomForestRegressor #모델링

X_train=train_weekdays[input_var]
random.seed(1656) #동일한 샘플링하기 위한 시드번호
train_list=random.sample(list(range(X_train.shape[0])), int(round(X_train.shape[0]*0.01,0)) )
# train data의 1% 데이터로 최적의 parameter 찾기

X_train=train_weekdays[input_var]
X_train=X_train.iloc[train_list,:]
y_train=train_weekdays[target]
y_train=y_train.iloc[train_list,:]

X_test=test_weekdays[input_var]

X_train.shape, y_train.shape

((3173, 9), (3173, 1))

In [31]:
X_train.head()

in_out  latitude  longitude  68a  810a  1012a  68b  810b  1012b
327801       0  33.45580  126.44179  0.0   0.0    0.0  0.0   0.0    1.0
338999       1  33.24362  126.42032  0.0   0.0    0.0  1.0   0.0    0.0
414242       0  33.26167  126.41228  4.0   0.0    0.0  0.0   0.0    0.0
347131       0  33.48815  126.49636  1.0   3.0    1.0  1.0   1.0    1.0
158116       0  33.48405  126.40876  0.0   0.0    1.0  0.0   0.0    0.0

GridSearCV & RandomForestRegression

random forest: 앙상블 학습 기반으로 한 관리 기계 학습 알고리즘
다중 의사결정 트리를 결합하여 tree forest 생성 ->
평균화를 사용하여 예측 정확도를 높이고 오버핏 제

In [33]:
# Create the parameter grid based on the results of random search 
param_grid = {
    'max_features': [2,3,5],
    'min_samples_leaf': [2,3],
    'min_samples_split': [2,4,6],
    'n_estimators': [100, 200,500]
}
# Create a based model

rf = RandomForestRegressor(random_state=1656) # 랜덤포레스트 모델을 정의한다.

# Instantiate the grid search model
grid_search = GridSearchCV(estimator = rf, param_grid = param_grid) # GridSearchCV를 정의한다.

grid_search.fit(X_train, y_train)

grid_search.best_params_ #학습 이후 최적의 paramter를 출력

/opt/conda/lib/python3.7/site-packages/sklearn/model_selection/_validation.py:531: DataConversionWarning: A column-vector y was passed when a 1d array was expected. Please change the shape of y to (n_samples,), for example using ravel().
  estimator.fit(X_train, y_train, **fit_params)
/opt/conda/lib/python3.7/site-packages/sklearn/model_selection/_validation.py:531: DataConversionWarning: A column-vector y was passed when a 1d array was expected. Please change the shape of y to (n_samples,), for example using ravel().
  estimator.fit(X_train, y_train, **fit_params)
/opt/conda/lib/python3.7/site-packages/sklearn/model_selection/_validation.py:531: DataConversionWarning: A column-vector y was passed when a 1d array was expected. Please change the shape of y to (n_samples,), for example using ravel().
  estimator.fit(X_train, y_train, **fit_params)
/opt/conda/lib/python3.7/site-packages/sklearn/model_selection/_validation.py:531: DataConversionWarning: A column-vector y was passed when a 

/opt/conda/lib/python3.7/site-packages/sklearn/model_selection/_validation.py:531: DataConversionWarning: A column-vector y was passed when a 1d array was expected. Please change the shape of y to (n_samples,), for example using ravel().
  estimator.fit(X_train, y_train, **fit_params)
/opt/conda/lib/python3.7/site-packages/sklearn/model_selection/_validation.py:531: DataConversionWarning: A column-vector y was passed when a 1d array was expected. Please change the shape of y to (n_samples,), for example using ravel().
  estimator.fit(X_train, y_train, **fit_params)
/opt/conda/lib/python3.7/site-packages/sklearn/model_selection/_validation.py:531: DataConversionWarning: A column-vector y was passed when a 1d array was expected. Please change the shape of y to (n_samples,), for example using ravel().
  estimator.fit(X_train, y_train, **fit_params)
/opt/conda/lib/python3.7/site-packages/sklearn/model_selection/_validation.py:531: DataConversionWarning: A column-vector y was passed when a 

/opt/conda/lib/python3.7/site-packages/sklearn/model_selection/_validation.py:531: DataConversionWarning: A column-vector y was passed when a 1d array was expected. Please change the shape of y to (n_samples,), for example using ravel().
  estimator.fit(X_train, y_train, **fit_params)
/opt/conda/lib/python3.7/site-packages/sklearn/model_selection/_validation.py:531: DataConversionWarning: A column-vector y was passed when a 1d array was expected. Please change the shape of y to (n_samples,), for example using ravel().
  estimator.fit(X_train, y_train, **fit_params)
/opt/conda/lib/python3.7/site-packages/sklearn/model_selection/_validation.py:531: DataConversionWarning: A column-vector y was passed when a 1d array was expected. Please change the shape of y to (n_samples,), for example using ravel().
  estimator.fit(X_train, y_train, **fit_params)
/opt/conda/lib/python3.7/site-packages/sklearn/model_selection/_validation.py:531: DataConversionWarning: A column-vector y was passed when a 

/opt/conda/lib/python3.7/site-packages/sklearn/model_selection/_validation.py:531: DataConversionWarning: A column-vector y was passed when a 1d array was expected. Please change the shape of y to (n_samples,), for example using ravel().
  estimator.fit(X_train, y_train, **fit_params)
/opt/conda/lib/python3.7/site-packages/sklearn/model_selection/_validation.py:531: DataConversionWarning: A column-vector y was passed when a 1d array was expected. Please change the shape of y to (n_samples,), for example using ravel().
  estimator.fit(X_train, y_train, **fit_params)
/opt/conda/lib/python3.7/site-packages/sklearn/model_selection/_validation.py:531: DataConversionWarning: A column-vector y was passed when a 1d array was expected. Please change the shape of y to (n_samples,), for example using ravel().
  estimator.fit(X_train, y_train, **fit_params)
/opt/conda/lib/python3.7/site-packages/sklearn/model_selection/_validation.py:531: DataConversionWarning: A column-vector y was passed when a 

/opt/conda/lib/python3.7/site-packages/sklearn/model_selection/_validation.py:531: DataConversionWarning: A column-vector y was passed when a 1d array was expected. Please change the shape of y to (n_samples,), for example using ravel().
  estimator.fit(X_train, y_train, **fit_params)
/opt/conda/lib/python3.7/site-packages/sklearn/model_selection/_validation.py:531: DataConversionWarning: A column-vector y was passed when a 1d array was expected. Please change the shape of y to (n_samples,), for example using ravel().
  estimator.fit(X_train, y_train, **fit_params)
/opt/conda/lib/python3.7/site-packages/sklearn/model_selection/_validation.py:531: DataConversionWarning: A column-vector y was passed when a 1d array was expected. Please change the shape of y to (n_samples,), for example using ravel().
  estimator.fit(X_train, y_train, **fit_params)
/opt/conda/lib/python3.7/site-packages/sklearn/model_selection/_validation.py:531: DataConversionWarning: A column-vector y was passed when a 

...

/opt/conda/lib/python3.7/site-packages/sklearn/model_selection/_validation.py:531: DataConversionWarning: A column-vector y was passed when a 1d array was expected. Please change the shape of y to (n_samples,), for example using ravel().
  estimator.fit(X_train, y_train, **fit_params)
/opt/conda/lib/python3.7/site-packages/sklearn/model_selection/_validation.py:531: DataConversionWarning: A column-vector y was passed when a 1d array was expected. Please change the shape of y to (n_samples,), for example using ravel().
  estimator.fit(X_train, y_train, **fit_params)
/opt/conda/lib/python3.7/site-packages/sklearn/model_selection/_validation.py:531: DataConversionWarning: A column-vector y was passed when a 1d array was expected. Please change the shape of y to (n_samples,), for example using ravel().
  estimator.fit(X_train, y_train, **fit_params)
/opt/conda/lib/python3.7/site-packages/sklearn/model_selection/_validation.py:531: DataConversionWarning: A column-vector y was passed when a 

/opt/conda/lib/python3.7/site-packages/sklearn/model_selection/_validation.py:531: DataConversionWarning: A column-vector y was passed when a 1d array was expected. Please change the shape of y to (n_samples,), for example using ravel().
  estimator.fit(X_train, y_train, **fit_params)
/opt/conda/lib/python3.7/site-packages/sklearn/model_selection/_validation.py:531: DataConversionWarning: A column-vector y was passed when a 1d array was expected. Please change the shape of y to (n_samples,), for example using ravel().
  estimator.fit(X_train, y_train, **fit_params)
/opt/conda/lib/python3.7/site-packages/sklearn/model_selection/_validation.py:531: DataConversionWarning: A column-vector y was passed when a 1d array was expected. Please change the shape of y to (n_samples,), for example using ravel().
  estimator.fit(X_train, y_train, **fit_params)
/opt/conda/lib/python3.7/site-packages/sklearn/model_selection/_validation.py:531: DataConversionWarning: A column-vector y was passed when a 

/opt/conda/lib/python3.7/site-packages/sklearn/model_selection/_validation.py:531: DataConversionWarning: A column-vector y was passed when a 1d array was expected. Please change the shape of y to (n_samples,), for example using ravel().
  estimator.fit(X_train, y_train, **fit_params)
/opt/conda/lib/python3.7/site-packages/sklearn/model_selection/_validation.py:531: DataConversionWarning: A column-vector y was passed when a 1d array was expected. Please change the shape of y to (n_samples,), for example using ravel().
  estimator.fit(X_train, y_train, **fit_params)
/opt/conda/lib/python3.7/site-packages/sklearn/model_selection/_validation.py:531: DataConversionWarning: A column-vector y was passed when a 1d array was expected. Please change the shape of y to (n_samples,), for example using ravel().
  estimator.fit(X_train, y_train, **fit_params)
/opt/conda/lib/python3.7/site-packages/sklearn/model_selection/_validation.py:531: DataConversionWarning: A column-vector y was passed when a 

/opt/conda/lib/python3.7/site-packages/sklearn/model_selection/_validation.py:531: DataConversionWarning: A column-vector y was passed when a 1d array was expected. Please change the shape of y to (n_samples,), for example using ravel().
  estimator.fit(X_train, y_train, **fit_params)
/opt/conda/lib/python3.7/site-packages/sklearn/model_selection/_validation.py:531: DataConversionWarning: A column-vector y was passed when a 1d array was expected. Please change the shape of y to (n_samples,), for example using ravel().
  estimator.fit(X_train, y_train, **fit_params)
/opt/conda/lib/python3.7/site-packages/sklearn/model_selection/_validation.py:531: DataConversionWarning: A column-vector y was passed when a 1d array was expected. Please change the shape of y to (n_samples,), for example using ravel().
  estimator.fit(X_train, y_train, **fit_params)
/opt/conda/lib/python3.7/site-packages/sklearn/model_selection/_validation.py:531: DataConversionWarning: A column-vector y was passed when a 

{'max_features': 2,
 'min_samples_leaf': 3,
 'min_samples_split': 2,
 'n_estimators': 100}

{'max_features': 2,
 'min_samples_leaf': 3,
 'min_samples_split': 2,
 'n_estimators': 100}

In [34]:
#전체 데이터로 적용
X_train=train_weekdays[input_var]
y_train=train_weekdays[target]

X_test=test_weekdays[input_var]

X_train.shape, y_train.shape, X_test.shape

((317330, 9), (317330, 1), (177669, 9))

In [35]:
# best_params_를 통해서 나온 값을 투입
rf = RandomForestRegressor(max_features=2,min_samples_leaf=3,min_samples_split=2,n_estimators=100,random_state=1656)

rf.fit(X_train,y_train) #학습 

test_weekdays['18~20_ride'] = rf.predict(X_test) #예측값 생성 후, test['18~20_ride']에 집어 넣는다.

/opt/conda/lib/python3.7/site-packages/ipykernel_launcher.py:4: DataConversionWarning: A column-vector y was passed when a 1d array was expected. Please change the shape of y to (n_samples,), for example using ravel().
  after removing the cwd from sys.path.
/opt/conda/lib/python3.7/site-packages/ipykernel_launcher.py:6: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  


In [36]:
test_weekdays.head()

id        date  bus_route_id  in_out  station_code  station_name  \
0  415423  2019-10-01       4270000       1           344         제주썬호텔   
1  415424  2019-10-01       4270000       1           357          한라병원   
2  415425  2019-10-01       4270000       1           432          정존마을   
3  415426  2019-10-01       4270000       0          1579  제주국제공항(600번)   
4  415427  2019-10-01       4270000       0          1636          롯데호텔   

   latitude  longitude  6~7_ride  7~8_ride  8~9_ride  9~10_ride  10~11_ride  \
0  33.48990  126.49373       4.0       4.0       7.0        2.0         9.0   
1  33.48944  126.48508       1.0       6.0       6.0        1.0         8.0   
2  33.48181  126.47352       2.0       4.0       2.0        2.0         2.0   
3  33.50577  126.49252       1.0      11.0      18.0        8.0        26.0   
4  33.24872  126.41032       0.0       0.0       0.0        0.0         0.0   

   11~12_ride  6~7_takeoff  7~8_takeoff  8~9_takeoff  9~10_takeoff  \
0         1.0          0.0          0.0          0.0           0.0   
1        11.0          0.0          0.0          0.0           0.0   
2         1.0          0.0          0.0          0.0           0.0   
3        20.0          0.0          0.0          0.0           0.0   
4         0.0          0.0          0.0          0.0           1.0   

   10~11_takeoff  11~12_takeoff   68a  810a  1012a  68b  810b  1012b  weekday  \
0            0.0            1.0   8.0   9.0   10.0  0.0   0.0    1.0        1   
1            0.0            0.0   7.0   7.0   19.0  0.0   0.0    0.0        1   
2            0.0            0.0   6.0   4.0    3.0  0.0   0.0    0.0        1   
3            0.0            0.0  12.0  26.0   46.0  0.0   0.0    0.0        1   
4            0.0            0.0   0.0   0.0    0.0  0.0   1.0    0.0        1   

             location  18~20_ride  
0   33.4899,126.49373    9.483706  
1  33.48944,126.48508    9.619439  
2  33.48181,126.47352    3.872762  
3  33.50577,126.49252   42.483813  
4  33.24872,126.41032    0.101409

In [47]:
test_value = pd.DataFrame(test_weekdays.value_counts())
test_value

0
id     date       bus_route_id in_out station_code station_name latitude longitude 6~7_ride 7~8_ride 8~9_ride 9~10_ride 10~11_ride 11~12_ride 6~7_takeoff 7~8_takeoff 8~9_takeoff 9~10_takeoff 10~11_takeoff 11~12_takeoff 68a 810a 1012a 68b 810b 1012b weekday location                     18~20_ride   
415423 2019-10-01 4270000      1      344          제주썬호텔        33.48990 126.49373 4.0      4.0      7.0      2.0       9.0        1.0        0.0         0.0         0.0         0.0          0.0           1.0           8.0 9.0  10.0  0.0 0.0  1.0   1       33.4899,126.49373            9.483706    1
559076 2019-10-11 23050000     0      1443         하귀휴먼시아입구     33.48573 126.41515 0.0      0.0      1.0      0.0       0.0        0.0        0.0         0.0         2.0         0.0          0.0           0.0           0.0 1.0  0.0   0.0 2.0  0.0   4       33.48573,126.41515           0.087363    1
559068 2019-10-11 23050000     0      577          광평           33.48389 126.46841 0.0      2.0      0.0      0.0       0.0        2.0        0.0         0.0         0.0         1.0          2.0           1.0           2.0 0.0  2.0   0.0 1.0  3.0   4       33.48389,126.46841           1.479915    1
559069 2019-10-11 23050000     0      620          다호마을         33.50458 126.49625 0.0      0.0      0.0      0.0       1.0        0.0        0.0         0.0         0.0         0.0          0.0           0.0           0.0 0.0  1.0   0.0 0.0  0.0   4       33.50458,126.49625           0.361921    1
559070 2019-10-11 23050000     0      622          백록초등학교       33.48541 126.47151 0.0      2.0      1.0      3.0       0.0        1.0        0.0         0.0         1.0         1.0          0.0           0.0           2.0 4.0  1.0   0.0 2.0  0.0   4       33.485409999999995,126.47151 2.419075    1
...                                                                                                                                                                                                                                                                                                      ..
499850 2019-10-07 23370000     0      548          아라초등학교       33.47748 126.54470 0.0      3.0      0.0      0.0       0.0        0.0        0.0         0.0         0.0         2.0          0.0           0.0           3.0 0.0  0.0   0.0 2.0  0.0   0       33.47748,126.5447            1.228423    1
499851 2019-10-07 23370000     0      549          영평상동마을회관     33.47666 126.56822 0.0      0.0      0.0      0.0       0.0        0.0        0.0         0.0         1.0         0.0          0.0           0.0           0.0 0.0  0.0   0.0 1.0  0.0   0       33.476659999999995,126.56822 0.049004    1
499852 2019-10-07 23370000     0      598          금천마을         33.47849 126.55348 0.0      3.0      0.0      0.0       0.0        0.0        0.0         1.0         0.0         0.0          0.0           0.0           3.0 0.0  0.0   1.0 0.0  0.0   0       33.47849,126.55348           0.213518    1
499853 2019-10-07 23370000     0      662          월평마을         33.46968 126.57539 0.0      0.0      0.0      0.0       0.0        0.0        0.0         3.0         1.0         0.0          0.0           0.0           0.0 0.0  0.0   3.0 1.0  0.0   0       33.46968,126.57538999999998  0.224948    1
643592 2019-10-16 32820000     0      6115100      서귀포시외버스터미널   33.24873 126.50799 0.0      0.0      0.0      0.0       0.0        0.0        0.0         0.0         3.0         0.0          0.0           0.0           0.0 0.0  0.0   0.0 3.0  0.0   2       33.24873,126.50799           0.007025    1

[177669 rows x 1 columns]

> 2. LGBMRegressor

In [39]:
train_weekdays.head()

id        date  bus_route_id  in_out  station_code  station_name  \
11538  11538  2019-09-02       4270000       1           344         제주썬호텔   
11539  11539  2019-09-02       4270000       1           357          한라병원   
11540  11540  2019-09-02       4270000       1           432          정존마을   
11541  11541  2019-09-02       4270000       0          1579  제주국제공항(600번)   
11542  11542  2019-09-02       4270000       0          1636          롯데호텔   

       latitude  longitude  6~7_ride  7~8_ride  8~9_ride  9~10_ride  \
11538  33.48990  126.49373       1.0       8.0       3.0        3.0   
11539  33.48944  126.48508       1.0       3.0       1.0        2.0   
11540  33.48181  126.47352       0.0       4.0       0.0        1.0   
11541  33.50577  126.49252       1.0      12.0      17.0       21.0   
11542  33.24872  126.41032       0.0       0.0       0.0        0.0   

       10~11_ride  11~12_ride  6~7_takeoff  7~8_takeoff  8~9_takeoff  \
11538         0.0         4.0          0.0          0.0          0.0   
11539         8.0         9.0          0.0          0.0          0.0   
11540         0.0         1.0          0.0          0.0          0.0   
11541        19.0        16.0          0.0          0.0          0.0   
11542         0.0         0.0          0.0          0.0          0.0   

       9~10_takeoff  10~11_takeoff  11~12_takeoff  18~20_ride   68a  810a  \
11538           0.0            0.0            0.0         1.0   9.0   6.0   
11539           0.0            0.0            0.0         6.0   4.0   3.0   
11540           0.0            1.0            0.0         2.0   4.0   1.0   
11541           0.0            0.0            2.0        62.0  13.0  38.0   
11542           3.0            0.0            0.0         0.0   0.0   0.0   

       1012a  68b  810b  1012b  weekday            location  
11538    4.0  0.0   0.0    0.0        0   33.4899,126.49373  
11539   17.0  0.0   0.0    0.0        0  33.48944,126.48508  
11540    1.0  0.0   0.0    1.0        0  33.48181,126.47352  
11541   35.0  0.0   0.0    2.0        0  33.50577,126.49252  
11542    0.0  0.0   3.0    0.0        0  33.24872,126.41032

In [40]:
# 학습데이터를 검증데이터로 분리하고 LGBM Regressor로 학습
ftr_weekdays = train_weekdays[input_var]
target_weekdays = train_weekdays[target]

In [41]:
from sklearn.model_selection import train_test_split

train_x, valid_x, train_y, valid_y = train_test_split(ftr_weekdays, target_weekdays, test_size=0.3, random_state=3055)
train_x.shape, valid_x.shape

((222131, 9), (95199, 9))

In [42]:
train_y.shape, valid_y.shape

((222131, 1), (95199, 1))

In [43]:
train_y.head()

18~20_ride
75757          0.0
20524          0.0
265027         1.0
335446         0.0
44652          6.0

In [44]:
from lightgbm import LGBMRegressor

lgbm = LGBMRegressor(num_iterations = 1000,
                     learning_rate = 0.05,
                     boosting = 'dart',
                     Metric = 'regression_l2', n_jobs=-1
        )

lgbm.fit(ftr_weekdays, target_weekdays)

/opt/conda/lib/python3.7/site-packages/lightgbm/engine.py:151: UserWarning: Found `num_iterations` in params. Will use it instead of argument
  warnings.warn("Found `{}` in params. Will use it instead of argument".format(alias))


[LightGBM] [Warning] Unknown parameter: Metric
[LightGBM] [Warning] boosting is set=dart, boosting_type=gbdt will be ignored. Current value: boosting=dart


LGBMRegressor(Metric='regression_l2', boosting='dart', learning_rate=0.05,
              num_iterations=1000)

In [45]:
target_pred = lgbm.predict(X)

NameError: name 'X' is not defined

In [ ]:
np.sqrt(mean_squared_error(target_weekdays, target_pred))

In [ ]:
target_pred = lgbm.predict(test_weekdays[input_var_0])

In [ ]:
from lightgbm import plot_importance
plot_importance(clf, figsize=(16, 32))